In [1]:
!jt -t grade3 -fs 90 -tfs 15 -nfs 115 -cellw 80% -T
import ROOT as R
import array
import numpy as np
from math import log10
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from influxdb import InfluxDBClient
from plotly.subplots import make_subplots
import datetime
import FTT_spectrum as FFT_script
import log_loader_time
import deode_TL

import os
%jsroot on
decode_istance=deode_TL.reader("raw_data/")

def get_last_file(mypath):
    onlyfiles = [f for f in os.listdir(mypath) if (os.path.isfile(os.path.join(mypath, f)) and 'missing_frames' not in f and "efine" in f)]
    onlyfiles.sort()
    return (os.path.join(mypath,onlyfiles[-1]))
def decode_data(filename,gemroc):
    out_name=("root_files/")+filename.split("raw_data/")[1].split(".")[0]+".root"
    decode_istance.write_root(filename,gemroc, 0, 0, out_name)

Welcome to JupyROOT 6.16/00


In [2]:
c=R.TCanvas()

# Analisi rumore triggerless

## Dati Pechino

Ora i dati da Pechino sono più chiari e leggibili. Ora che sono più sicuro dei risultati, ho portato un po' avanti l'analisi. Dividendola per "domini" di frequenza. Metto sia il grafico desintà di potenza spettrale vs Hz, dove si vedono meglio gli andamenti, sia quello trasformata vs Hz, dove si vedono meglio i picchi

#### ~kHz

In [3]:
f=R.TFile("/media/alb/Removibile/dati/416/sub_0_G_4.root")
R.gStyle.SetOptStat(0)
ext_1 =0
ext_2=30
f.tree.Draw("lcl_timestamp")
c.Draw()

In [4]:
h_trans_hz_1, h_spec_0, h_ori=FFT_script.extract_spectrum(f.tree,20000,ext_1,ext_2)

In [5]:
h_spec_0.Draw()
c.Draw()

In [6]:
h_trans_hz_1.Draw()
c.Draw()

A basse frequenza si vede qualcosa di simile alla situazione vista a Ferrara senza schermatura dei cavi short haul HV, ovvero dei picchi a multipli di 50 Hz. Direi che eseguire la stessa operazione che abbiamo provato a fare a Ferrara potrebbe giovare.

#### ~10kHz

In [7]:
ext_1 =13
ext_2=13.5
h_trans_hz_1, h_spec_0, h_ori=FFT_script.extract_spectrum(f.tree,200000,ext_1,ext_2)

ZeroDivisionError: float division by zero

Warning in <TFile::Append>: Replacing existing TH1: out_MAG (Potential memory leak).
Warning in <TFile::Append>: Replacing existing TH1: out_MAG (Potential memory leak).
Warning in <TFile::Append>: Replacing existing TH1: h_trasf_hz_2 (Potential memory leak).
Warning in <TFile::Append>: Replacing existing TH1: h_spec (Potential memory leak).


In [ ]:
h_spec_0.Draw()
c.Draw()

In [ ]:
h_trans_hz_1.Draw()
c.Draw()

Zoommando sulla zona >24 kHz, si nota bene un aumento di noise passante, forse c'è qualche elemento che filtra fino a 24kHz circa. Non noto picchi particolari

#### ~100kHz

In [ ]:
ext_1 =13
ext_2=13.2
h_trans_hz_1, h_spec_0, h_ori=FFT_script.extract_spectrum(f.tree,2000000,ext_1,ext_2)

In [ ]:
h_spec_0.Draw()
c.Draw()

In [ ]:
h_trans_hz_1.Draw()
c.Draw()

Non saperi commentare le bande, ma c'è un picco a 937.5 kHz che sembra di natura "umana". E' una delle frequenze usate dal protoccolo JTAG, potrebbe essere questo?

#### ~10MHz

In [ ]:
ext_1 =13
ext_2=13.001
h_trans_hz_1, h_spec_0, h_ori=FFT_script.extract_spectrum(f.tree,200000000,ext_1,ext_2)

In [ ]:
h_spec_0.Draw()
c.Draw()

In [ ]:
h_trans_hz_1.Draw()
c.Draw()

Sulle decine di MHz si nota benissimo il picco a 40 MHz, che suppongo essere indotto dal nostro BESIII clock distribuito fra le GEMROC. Mi sembra un picco un po' infame, perchè a questa frequenza abbastanza alta la probabilità che si infili nella zona di segnale diventa abbastanza alta.

 # Conclusioni

Il picco a 2441 Hz era dovuto a un mio errore di codifica. Ora che è risolto, i tool di analisi spettrale mi sembrano affidabili. Sul setup, mi sembra di capire che migliorare lo shielding dei cavi HV potrebbe miglirare le prestazioni per quanto riguarda il noise a bassa frequenza, mentre forse si potrebbe fare qualche tentativo di schermatura aggiuntiva del BESIII clock per eliminare o limitare il picco a 40 MHz. <br> Per studiare a frequenze maggiori devo introdurre nella mia analisi la calibrazione del Tfine, visto che per ora siamo limitati dal Tcoarse (che campiona come il clock a 160 MHz).
